In [26]:
import netCDF4 as nc
import numpy as np
import pandas as pd 
import os
import plotly.express as px
import json
import pycountry
import dash
import dash_core_components as dcc
import dash_html_components as html

path = 'E:/Users/LuoZN/Desktop/Data_vis'
file_name = 'GlobalLandTemperaturesByCountry.csv'

In [41]:
with open('./data/countries.geo.json') as response:
    countries = json.load(response)

In [28]:
len(countries["features"][31]['geometry']['coordinates'])

3

In [29]:
file_path = os.path.join(path,file_name)
temperaturebycountry = pd.read_csv(file_path)
del temperaturebycountry['AverageTemperatureUncertainty']
temperaturebycountry['dt'] = pd.to_datetime(temperaturebycountry['dt']) 
temperaturebycountry['year'] = [date.year for date in temperaturebycountry.dt]
del temperaturebycountry['dt']
temperaturebycountry =  temperaturebycountry.groupby(['Country','year']).mean()
temperaturebycountry['country'] = [p[0] for p in temperaturebycountry.index]
temperaturebycountry['year'] = [p[1] for p in temperaturebycountry.index]
temperaturebycountry = temperaturebycountry.reset_index(drop=True)
temperaturebycountry['country'] = [name.split(' (')[0] for name in temperaturebycountry['country']]
temperaturebycountry=temperaturebycountry.drop(temperaturebycountry[temperaturebycountry['country']=='Taiwan'].index)

temperaturebycountry.query("country=='Taiwan'")

Empty DataFrame
Columns: [AverageTemperature, country, year]
Index: []

In [31]:
alpha_3 = {}
for c in list(set(temperaturebycountry['country'])):
    try:
        a = pycountry.countries.get(name = c).alpha_3
        alpha_3[c] = a
    except:
        try:
            a = pycountry.countries.get(common_name = c).alpha_3
            alpha_3[c] = a
        except:
            pass

In [32]:
temperaturebycountry['alpha_3'] = temperaturebycountry['country'].map(alpha_3)
temperaturebycountry

AverageTemperature      country  year alpha_3
0               18.379571  Afghanistan  1838     AFG
1                     NaN  Afghanistan  1839     AFG
2               13.413455  Afghanistan  1840     AFG
3               13.997600  Afghanistan  1841     AFG
4               15.154667  Afghanistan  1842     AFG
...                   ...          ...   ...     ...
48238            6.489083        Åland  2009     NaN
48239            4.861917        Åland  2010     NaN
48240            7.170750        Åland  2011     NaN
48241            6.063917        Åland  2012     NaN
48242            6.229750        Åland  2013     NaN

[48070 rows x 4 columns]

In [34]:
temp = temperaturebycountry[temperaturebycountry['year']==1900]
temp

AverageTemperature         country  year alpha_3
62              13.749333     Afghanistan  1900     AFG
226             23.991500          Africa  1900     NaN
497             13.068583         Albania  1900     ALB
724             22.864167         Algeria  1900     DZA
871             26.273500  American Samoa  1900     ASM
...                   ...             ...   ...     ...
47392           22.263750  Western Sahara  1900     ESH
47530           25.990583           Yemen  1900     YEM
47694           21.374083          Zambia  1900     ZMB
47858           21.275833        Zimbabwe  1900     ZWE
48129            4.547833           Åland  1900     NaN

[237 rows x 4 columns]

In [39]:
#fig = px.choropleth(temperaturebycountry, locations="country",locationmode='country names', color="AverageTemperature", hover_name="country", animation_frame="year", range_color=[20,80],projection="orthographic")
fig = px.choropleth(temperaturebycountry,geojson=countries, locations='alpha_3', color='AverageTemperature',
                            featureidkey="id",hover_name='country',
                           color_continuous_scale="Viridis"            
                          )
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

In [49]:
type(countries)

dict

In [60]:
longitude = file_obj.variables['longitude']
latitude = file_obj.variables['latitude']
time = file_obj.variables['time']
land_mask = file_obj.variables['land_mask']
temperature = file_obj.variables['temperature']
climatology = file_obj.variables['climatology']

# scatter geo 实现

In [62]:
tp = np.array(temperature)
tp = pd.DataFrame(tp)
tp['time_id']=tp.index
tp = tp.melt(id_vars='time_id')
tp = tp.rename(columns={'variable':'pt_id','value':'temperature'})

lat,lon = np.array(latitude),np.array(longitude)
lat,lon = pd.DataFrame(lat),pd.DataFrame(lon)
lat['pt_id'] = lat.index
lat = lat.rename(columns={0:'latitude'})
lon['pt_id'] = lon.index
lon = lon.rename(columns={0:'longitude'})

t = np.array(time)
t = pd.DataFrame(t)
t['time_id'] = t.index
t = t.rename(columns={0:'time'})

D:\Users\LuoZN\Anaconda3\envs\py36\lib\site-packages\ipykernel_launcher.py:1: RuntimeWarning:

invalid value encountered in less

D:\Users\LuoZN\Anaconda3\envs\py36\lib\site-packages\ipykernel_launcher.py:1: RuntimeWarning:

invalid value encountered in greater



In [63]:
df = tp.merge(t,how='left',on='time_id').merge(lat,how='left',on='pt_id').merge(lon,how='left',on='pt_id')
df 

time_id pt_id  temperature         time   latitude   longitude
0               0     0          NaN  1750.041667  82.788071  -83.571426
1               1     0          NaN  1750.125000  82.788071  -83.571426
2               2     0          NaN  1750.208333  82.788071  -83.571426
3               3     0          NaN  1750.291667  82.788071  -83.571426
4               4     0          NaN  1750.375000  82.788071  -83.571426
...           ...   ...          ...          ...        ...         ...
17813515     3235  5497    -0.661482  2019.625000 -89.215027  120.000000
17813516     3236  5497    -0.035485  2019.708333 -89.215027  120.000000
17813517     3237  5497    -0.595212  2019.791667 -89.215027  120.000000
17813518     3238  5497     0.651016  2019.875000 -89.215027  120.000000
17813519     3239  5497     0.251135  2019.958333 -89.215027  120.000000

[17813520 rows x 6 columns]

In [64]:
df['pt'] = [(lat,lon) for lat,lon in zip(df['latitude'],df['longitude'])]
df['year']=df['time']//1
del df['pt_id']
del df['time_id']
del df['latitude']
del df['longitude']
del df['time']
df 

temperature                                       pt    year
0                 NaN  (82.78807067871094, -83.57142639160156)  1750.0
1                 NaN  (82.78807067871094, -83.57142639160156)  1750.0
2                 NaN  (82.78807067871094, -83.57142639160156)  1750.0
3                 NaN  (82.78807067871094, -83.57142639160156)  1750.0
4                 NaN  (82.78807067871094, -83.57142639160156)  1750.0
...               ...                                      ...     ...
17813515    -0.661482              (-89.21502685546875, 120.0)  2019.0
17813516    -0.035485              (-89.21502685546875, 120.0)  2019.0
17813517    -0.595212              (-89.21502685546875, 120.0)  2019.0
17813518     0.651016              (-89.21502685546875, 120.0)  2019.0
17813519     0.251135              (-89.21502685546875, 120.0)  2019.0

[17813520 rows x 3 columns]

In [65]:
df = df.groupby(by=['pt','year']).mean()
df

temperature
pt                                       year               
(-89.21502685546875, -120.0)             1750.0          NaN
                                         1751.0          NaN
                                         1752.0          NaN
                                         1753.0          NaN
                                         1754.0          NaN
...                                                      ...
(82.78807067871094, -19.285715103149414) 2015.0     2.027671
                                         2016.0     3.652489
                                         2017.0     2.202293
                                         2018.0     2.950691
                                         2019.0     2.164294

[1484460 rows x 1 columns]

In [66]:
df['latitude'] = [p[0][0] for p in df.index]
df['longitude'] = [p[0][1] for p in df.index]
df['year'] = [p[1] for p in df.index]
df = df.reset_index(drop=True)
df

temperature   latitude   longitude    year
0                NaN -89.215027 -120.000000  1750.0
1                NaN -89.215027 -120.000000  1751.0
2                NaN -89.215027 -120.000000  1752.0
3                NaN -89.215027 -120.000000  1753.0
4                NaN -89.215027 -120.000000  1754.0
...              ...        ...         ...     ...
1484455     2.027671  82.788071  -19.285715  2015.0
1484456     3.652489  82.788071  -19.285715  2016.0
1484457     2.202293  82.788071  -19.285715  2017.0
1484458     2.950691  82.788071  -19.285715  2018.0
1484459     2.164294  82.788071  -19.285715  2019.0

[1484460 rows x 4 columns]

In [35]:
import plotly.express as px
#df = px.data.gapminder()
fig = px.scatter_geo(df, lat = 'latitude', lon = 'longitude', color="temperature",
               projection="orthographic",animation_frame ='year')
fig.show()

# 3d scatter实现

In [61]:
def get_xyz(latitude,longitude,R):
    lat = latitude/np.pi
    long = longitude/np.pi
    x = R * np.math.cos(lat) * np.math.cos(long)
    y = R * np.math.cos(lat) * np.math.sin(long)
    z = R * np.math.sin(lat)
    return x,y,z
get_xyz(0,120,40)

(35.14016275371421, 19.109394591207668, 0.0)

In [100]:
import plotly.express as px
#df = px.data.election()
fig = px.scatter_3d(df, x="x", y="y", z="z",color='temperature')
fig.show()

In [126]:
from geopy.geocoders import Nominatim

geolocator = Nominatim()
location = geolocator.reverse("39.9073426, 60.391264649167")   # 传入纬度、经度字符串
print(location.address)
print((location.latitude,location.longitude))
print(location.altitude)
print(location.raw)

D:\Users\LuoZN\Anaconda3\envs\py36\lib\site-packages\ipykernel_launcher.py:3: DeprecationWarning:

Using Nominatim with the default "geopy/1.21.0" `user_agent` is strongly discouraged, as it violates Nominatim's ToS https://operations.osmfoundation.org/policies/nominatim/ and may possibly cause 403 and 429 HTTP errors. Please specify a custom `user_agent` with `Nominatim(user_agent="my-application")` or by overriding the default `user_agent`: `geopy.geocoders.options.default_user_agent = "my-application"`. In geopy 2.0 this will become an exception.



Daşoguz welaýaty, Türkmenistan
(41.1582796, 58.71143523158547)
0.0
{'place_id': 235089873, 'licence': 'Data © OpenStreetMap contributors, ODbL 1.0. https://osm.org/copyright', 'osm_type': 'relation', 'osm_id': 223028, 'lat': '41.1582796', 'lon': '58.71143523158547', 'display_name': 'Daşoguz welaýaty, Türkmenistan', 'address': {'state': 'Daşoguz welaýaty', 'country': 'Türkmenistan', 'country_code': 'tm'}, 'boundingbox': ['39.4672693', '42.797427', '56.4293754', '60.9448991']}


In [ ]:
import plotly.graph_objects as go
import numpy as np

# Download data set from plotly repo
pts = np.loadtxt(np.DataSource().open('https://raw.githubusercontent.com/plotly/datasets/master/mesh_dataset.txt'))
x, y, z = pts.T

fig = go.Figure(data=[go.Mesh3d(x=x, y=y, z=z, color='lightpink', opacity=0.50)])
fig.show()